## 기본 베이지 DNN

In [1]:
import pandas as pd
import numpy as np
import torch
import torch.nn as nn
from sklearn.preprocessing import MinMaxScaler
from tensorflow.python.keras.models import Sequential
from tensorflow.python.keras.layers import Dense,Dropout,Activation
from torch.utils.data import TensorDataset, DataLoader
from tensorflow.python.keras import metrics
from tensorflow.python import keras
import tensorflow as tf
import matplotlib.pyplot as plt
from imblearn.over_sampling import SMOTE

In [2]:
%matplotlib inline

In [3]:
df=pd.read_excel('./modeling_data/Continous_2weeks_14day_7term.xlsx')

In [4]:
df.head()

0     1          2     3    4    5    6      7  Label
0  #AAGQKY  45.0  20.544193  72.0  0.0  0.0  0.0  148.0      0
1  #AAGQKY  45.0  20.544193  72.0  0.0  0.0  0.0  148.0      0
2  #AAGQKY  45.0  20.544193  72.0  0.0  0.0  0.0  148.0      0
3  #AAGQKY  45.0  20.544193  72.0  0.0  0.0  0.0  148.0      0
4  #AAGQKY  45.0  20.544193  72.0  0.0  0.0  0.0  148.0      0

In [5]:
X=df.iloc[:,1:7]
y=df.loc[:,"Label"]

In [6]:
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split

In [7]:
scaler = StandardScaler()

# X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.30)
X_train=X.iloc[:2475,:]
X_test=X.iloc[2475:,:]

y_train=y.iloc[:2475]
y_test=y.iloc[2475:]

X_train = scaler.fit_transform(X_train)
X_test = scaler.transform(X_test)

In [8]:
X.iloc[2474,0:7]

1      43.900000
2      18.510710
3    1830.100000
4       0.000000
5    7425.846154
6       0.000000
Name: 2474, dtype: float64

In [9]:
smote = SMOTE(random_state=0)
X_train_over,y_train_over = smote.fit_resample(X_train,y_train)
print('SMOTE 적용 전 학습용 피처/레이블 데이터 세트: ', X_train.shape, y_train.shape)
print('SMOTE 적용 후 학습용 피처/레이블 데이터 세트: ', X_train_over.shape, y_train_over.shape)
print('SMOTE 적용 전 레이블 값 분포: \n', pd.Series(y_train).value_counts())
print('SMOTE 적용 후 레이블 값 분포: \n', pd.Series(y_train_over).value_counts())

SMOTE 적용 전 학습용 피처/레이블 데이터 세트:  (2475, 6) (2475,)
SMOTE 적용 후 학습용 피처/레이블 데이터 세트:  (5136, 6) (5136,)
SMOTE 적용 전 레이블 값 분포: 
 0    1712
1     429
2     334
Name: Label, dtype: int64
SMOTE 적용 후 레이블 값 분포: 
 0    1712
1    1712
2    1712
Name: Label, dtype: int64


In [10]:
X_train = torch.FloatTensor(X_train_over)
X_test = torch.FloatTensor(X_test)
y_train = torch.LongTensor(y_train_over)
y_test = torch.LongTensor(y_test.to_numpy())

In [11]:
train_dataset = TensorDataset(X_train, y_train)
test_dataset=TensorDataset(X_test, y_test)

In [12]:
train_dataloader = DataLoader(train_dataset, batch_size=44, shuffle=False)
test_dataloader = DataLoader(test_dataset, batch_size=44, shuffle=False)

In [13]:
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim


class DNNModel(nn.Module):
    def __init__(self):
        super(DNNModel, self).__init__()
        self.input_layer = nn.Linear(6, 128)
        self.hidden_layer1 = nn.Linear(128, 256)
        self.hidden_layer2 = nn.Linear(256, 128)
        self.output_layer   = nn.Linear(128,3)
        self.relu = nn.ReLU()
    
    
    
    def forward(self, x):
        out =  self.relu(self.input_layer(x))
        out =  self.relu(self.hidden_layer1(out))
        out =  self.relu(self.hidden_layer2(out))
        out =  self.output_layer(out)
        return out 
    
    

In [14]:
# device 설정 (cuda:0 혹은 cpu)
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
model = DNNModel() # Model 생성
model.to(device)   # device 에 로드 (cpu or cuda)

DNNModel(
  (input_layer): Linear(in_features=6, out_features=128, bias=True)
  (hidden_layer1): Linear(in_features=128, out_features=256, bias=True)
  (hidden_layer2): Linear(in_features=256, out_features=128, bias=True)
  (output_layer): Linear(in_features=128, out_features=3, bias=True)
  (relu): ReLU()
)

In [15]:
# 옵티마이저를 정의합니다. 옵티마이저에는 model.parameters()를 지정해야 합니다.
optimizer = optim.Adam(model.parameters(), lr=0.001)

# 손실함수(loss function)을 지정합니다. Multi-Class Classification 이기 때문에 CrossEntropy 손실을 지정하였습니다.
loss_fn = nn.CrossEntropyLoss()

In [16]:
from tqdm import tqdm  # Progress Bar 출력

In [17]:
def model_train(model, data_loader, loss_fn, optimizer, device):
    # 모델을 훈련모드로 설정합니다. training mode 일 때 Gradient 가 업데이트 됩니다. 반드시 train()으로 모드 변경을 해야 합니다.
    model.train()
    
    # loss와 accuracy 계산을 위한 임시 변수 입니다. 0으로 초기화합니다.
    running_loss = 0
    corr = 0
    
    # 예쁘게 Progress Bar를 출력하면서 훈련 상태를 모니터링 하기 위하여 tqdm으로 래핑합니다.
    prograss_bar = tqdm(data_loader)
    
    # mini-batch 학습을 시작합니다.
    for data, lbl in prograss_bar:
        # image, label 데이터를 device에 올립니다.
        data, lbl = data.to(device), lbl.to(device)
        # 누적 Gradient를 초기화 합니다.
        optimizer.zero_grad()
        
        # Forward Propagation을 진행하여 결과를 얻습니다.
        output = model(data)
        
        # 손실함수에 output, label 값을 대입하여 손실을 계산합니다.
        loss = loss_fn(output, lbl)
        
        # 오차역전파(Back Propagation)을 진행하여 미분 값을 계산합니다.
        loss.backward()
        
        # 계산된 Gradient를 업데이트 합니다.
        optimizer.step()
        
        # output의 max(dim=1)은 max probability와 max index를 반환합니다.
        # max probability는 무시하고, max index는 pred에 저장하여 label 값과 대조하여 정확도를 도출합니다.
        _, pred = output.max(dim=1)
        
        # pred.eq(lbl).sum() 은 정확히 맞춘 label의 합계를 계산합니다. item()은 tensor에서 값을 추출합니다.
        # 합계는 corr 변수에 누적합니다.
        corr += pred.eq(lbl).sum().item()
        
        # loss 값은 1개 배치의 평균 손실(loss) 입니다. data.size(0)은 배치사이즈(batch size) 입니다.
        # loss 와 data.size(0)를 곱하면 1개 배치의 전체 loss가 계산됩니다.
        # 이를 누적한 뒤 Epoch 종료시 전체 데이터셋의 개수로 나누어 평균 loss를 산출합니다.
        running_loss += loss.item() * data.size(0)
        
    # 누적된 정답수를 전체 개수로 나누어 주면 정확도가 산출됩니다.
    acc = corr / len(data_loader.dataset)
    
    # 평균 손실(loss)과 정확도를 반환합니다.
    # train_loss, train_acc
    return running_loss / len(data_loader.dataset), acc

In [18]:
def model_evaluate(model, data_loader, loss_fn, device):
    # model.eval()은 모델을 평가모드로 설정을 바꾸어 줍니다. 
    # dropout과 같은 layer의 역할 변경을 위하여 evaluation 진행시 꼭 필요한 절차 입니다.
    model.eval()
    
    # Gradient가 업데이트 되는 것을 방지 하기 위하여 반드시 필요합니다.
    with torch.no_grad():
        # loss와 accuracy 계산을 위한 임시 변수 입니다. 0으로 초기화합니다.
        corr = 0
        running_loss = 0
        
        # 배치별 evaluation을 진행합니다.
        for data, lbl in data_loader:
            # device에 데이터를 올립니다.
            data, lbl = data.to(device), lbl.to(device)
            
            # 모델에 Forward Propagation을 하여 결과를 도출합니다.
            output = model(data)
            
            # output의 max(dim=1)은 max probability와 max index를 반환합니다.
            # max probability는 무시하고, max index는 pred에 저장하여 label 값과 대조하여 정확도를 도출합니다.
            _, pred = output.max(dim=1)
            # pred.eq(lbl).sum() 은 정확히 맞춘 label의 합계를 계산합니다. item()은 tensor에서 값을 추출합니다.
            # 합계는 corr 변수에 누적합니다.
            corr += torch.sum(pred.eq(lbl)).item()
            
            # loss 값은 1개 배치의 평균 손실(loss) 입니다. data.size(0)은 배치사이즈(batch size) 입니다.
            # loss 와 data.size(0)를 곱하면 1개 배치의 전체 loss가 계산됩니다.
            # 이를 누적한 뒤 Epoch 종료시 전체 데이터셋의 개수로 나누어 평균 loss를 산출합니다.
            running_loss += loss_fn(output, lbl).item() * data.size(0)
        
        # validation 정확도를 계산합니다.
        # 누적한 정답숫자를 전체 데이터셋의 숫자로 나누어 최종 accuracy를 산출합니다.
        acc = corr / len(data_loader.dataset)
        
        # 결과를 반환합니다.
        # val_loss, val_acc
        return running_loss / len(data_loader.dataset), acc

In [19]:
# 최대 Epoch을 지정합니다.
num_epochs = 500

min_loss = np.inf

# Epoch 별 훈련 및 검증을 수행합니다.
for epoch in range(num_epochs):
    # Model Training
    # 훈련 손실과 정확도를 반환 받습니다.
    train_loss, train_acc = model_train(model, train_dataloader, loss_fn, optimizer, device)

    # 검증 손실과 검증 정확도를 반환 받습니다.
    val_loss, val_acc = model_evaluate(model, test_dataloader, loss_fn, device)   
    
    # val_loss 가 개선되었다면 min_loss를 갱신하고 model의 가중치(weights)를 저장합니다.
    if val_loss < min_loss:
        print(f'[INFO] val_loss has been improved from {min_loss:.5f} to {val_loss:.5f}. Saving Model!')
        min_loss = val_loss
        torch.save(model.state_dict(), 'DNNModel.pth')
    
    # Epoch 별 결과를 출력합니다.
    print(f'epoch {epoch+1:02d}, loss: {train_loss:.5f}, acc: {train_acc:.5f}, val_loss: {val_loss:.5f}, val_accuracy: {val_acc:.5f}')

 42%|█████████████████████████████████▌                                              | 49/117 [00:00<00:00, 489.89it/s]

torch.return_types.max(
values=tensor([0.2669, 0.2648, 0.2673, 0.2540, 0.2527, 0.2459, 0.2488, 0.2883, 0.2940,
        0.2755, 0.2541, 0.3716, 0.3649, 0.3556, 0.3696, 0.3673, 0.3635, 0.3615,
        0.3562, 0.3715, 0.3653, 0.3583, 0.1156, 0.1156, 0.1156, 0.1156, 0.1156,
        0.1156, 0.1156, 0.1156, 0.1156, 0.1156, 0.1156, 0.1332, 0.1332, 0.1332,
        0.1332, 0.1332, 0.1332, 0.1332, 0.1332, 0.1332, 0.1332, 0.1332]),
indices=tensor([2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2,
        2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2]))
torch.return_types.max(
values=tensor([0.1252, 0.1252, 0.1252, 0.1250, 0.1250, 0.1251, 0.1251, 0.1251, 0.1251,
        0.1251, 0.1251, 0.1622, 0.1608, 0.1601, 0.1589, 0.1562, 0.1564, 0.1581,
        0.1581, 0.1588, 0.1581, 0.1581, 0.1321, 0.1321, 0.1321, 0.1321, 0.1321,
        0.1321, 0.1321, 0.1321, 0.1321, 0.1321, 0.1321, 0.1867, 0.1838, 0.1811,
        0.1675, 0.1688, 0.1835, 0.1892, 0.1822, 0.1853, 0.2093, 0.

 43%|██████████████████████████████████▏                                             | 50/117 [00:00<00:00, 499.89it/s]

torch.return_types.max(
values=tensor([0.4197, 0.4070, 0.4102, 0.3859, 0.3879, 0.3731, 0.3782, 0.4845, 0.5510,
        0.4871, 0.3952, 0.5017, 0.4888, 0.4774, 0.4986, 0.5009, 0.4956, 0.4954,
        0.4792, 0.5047, 0.5114, 0.4858, 0.2968, 0.2968, 0.2968, 0.2968, 0.2968,
        0.2968, 0.2968, 0.2968, 0.2968, 0.2968, 0.2968, 0.3152, 0.3152, 0.3152,
        0.3152, 0.3152, 0.3152, 0.3152, 0.3152, 0.3152, 0.3152, 0.3152]),
indices=tensor([2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2,
        2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2]))
torch.return_types.max(
values=tensor([0.2592, 0.2591, 0.2591, 0.2591, 0.2591, 0.2591, 0.2591, 0.2591, 0.2591,
        0.2591, 0.2591, 0.3775, 0.3589, 0.3533, 0.3614, 0.3633, 0.3639, 0.3599,
        0.3599, 0.3607, 0.3648, 0.3678, 0.2671, 0.2671, 0.2671, 0.2671, 0.2671,
        0.2671, 0.2671, 0.2671, 0.2671, 0.2671, 0.2671, 0.4650, 0.4562, 0.4491,
        0.4176, 0.4212, 0.4564, 0.4717, 0.4516, 0.4634, 0.5172, 0.

 43%|██████████████████████████████████▏                                             | 50/117 [00:00<00:00, 499.89it/s]

...

torch.return_types.max(
values=tensor([-4.2653, -1.3286, -4.0223,  3.5012,  0.2964, -1.7898, -1.2844, -4.1282,
        -4.8465, -5.5239,  1.8353, -1.6806,  1.7396,  3.1274, -1.3693, -4.7146,
        -3.2391, -3.0067,  3.3542, -4.1626, -6.0094, -1.2555, 41.2377, 41.2377,
        41.2377, 41.2377, 41.2377, 41.2377, 41.2377, 41.2377, 41.2377, 41.2377,
        41.2377,  5.5496,  5.5496,  5.5496,  5.5496,  5.5496,  5.5496,  5.5496,
         5.5496,  5.5496,  5.5496,  5.5496]),
indices=tensor([1, 0, 0, 2, 2, 1, 0, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]))
torch.return_types.max(
values=tensor([ 3.8596,  3.8230,  3.8230,  3.5655,  3.5655,  3.7510,  3.7510,  3.7510,
         3.7510,  3.7510,  3.7510,  3.6117,  0.9270, -0.1761,  3.8986,  2.1014,
         1.0435,  0.3281,  0.3281,  0.5894,  0.3433,  0.8170,  9.6514,  9.6514,
         9.6514,  9.6514,  9.6514,  9.6514,  9.6514,  9.6514,  9.6514,  9.6514,
         9.651

 43%|██████████████████████████████████▏                                             | 50/117 [00:00<00:00, 494.93it/s]

torch.return_types.max(
values=tensor([-2.2747, -2.8874, -5.3920,  0.6613, -2.4667, -0.5829, -2.5058, -3.9570,
        -4.1760, -5.1742,  1.0961, -1.5902,  2.3175,  3.2596, -1.2331, -4.2531,
        -2.3298, -2.3511,  3.5934, -4.0507, -5.6796, -0.3988, 44.0888, 44.0888,
        44.0888, 44.0888, 44.0888, 44.0888, 44.0888, 44.0888, 44.0888, 44.0888,
        44.0888,  5.3650,  5.3650,  5.3650,  5.3650,  5.3650,  5.3650,  5.3650,
         5.3650,  5.3650,  5.3650,  5.3650]),
indices=tensor([1, 0, 0, 2, 2, 1, 0, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]))
torch.return_types.max(
values=tensor([ 3.2263,  3.1825,  3.1825,  2.9214,  2.9214,  3.1100,  3.1100,  3.1100,
         3.1100,  3.1100,  3.1100,  2.8291, -0.0362,  1.0278,  5.0910,  3.2341,
         2.1475,  0.9149,  0.9149,  1.3736,  2.5571,  2.2822,  7.8256,  7.8256,
         7.8256,  7.8256,  7.8256,  7.8256,  7.8256,  7.8256,  7.8256,  7.8256,
         7.825

100%|███████████████████████████████████████████████████████████████████████████████| 117/117 [00:00<00:00, 487.39it/s]

torch.return_types.max(
values=tensor([-2.8689, -1.5900, -3.8358, -1.4596, -3.0066, -1.7617, -1.1217, -2.7388,
        -1.7759, -4.7276,  2.6064, -2.3685,  0.8771,  3.0882, -2.0333, -4.7963,
        -3.5914, -3.9825,  2.6085, -4.8339, -6.2002, -1.6121, 42.1445, 42.1445,
        42.1445, 42.1445, 42.1445, 42.1445, 42.1445, 42.1445, 42.1445, 42.1445,
        42.1445,  5.5144,  5.5144,  5.5144,  5.5144,  5.5144,  5.5144,  5.5144,
         5.5144,  5.5144,  5.5144,  5.5144]),
indices=tensor([1, 0, 0, 0, 0, 1, 0, 1, 1, 1, 0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]))
torch.return_types.max(
values=tensor([ 3.4360,  3.3994,  3.3994,  3.1591,  3.1591,  3.3315,  3.3315,  3.3315,
         3.3315,  3.3315,  3.3315,  3.3503,  0.1564,  0.7538,  4.8943,  2.9092,
         1.8253,  0.0157,  0.0157,  0.5523,  1.9507,  2.0010,  8.1610,  8.1610,
         8.1610,  8.1610,  8.1610,  8.1610,  8.1610,  8.1610,  8.1610,  8.1610,
         8.161

## 저장한 가중치 로드 후 검증 성능 측정

In [20]:
# 모델에 저장한 가중치를 로드합니다.
model.load_state_dict(torch.load('DNNModel.pth'))

<All keys matched successfully>

In [21]:
# 최종 검증 손실(validation loss)와 검증 정확도(validation accuracy)를 산출합니다.
final_loss, final_acc = model_evaluate(model, test_dataloader, loss_fn, device)
print(f'evaluation loss: {final_loss:.5f}, evaluation accuracy: {final_acc:.5f}')

torch.return_types.max(
values=tensor([-0.0380, -0.0385, -0.0388, -0.0378, -0.0371, -0.0367, -0.0372, -0.0392,
        -0.0400, -0.0383, -0.0374, -0.0374, -0.0371, -0.0367, -0.0373, -0.0373,
        -0.0370, -0.0370, -0.0367, -0.0376, -0.0381, -0.0367,  0.0753,  0.0753,
         0.0753,  0.0753,  0.0753,  0.0753,  0.0753,  0.0753,  0.0753,  0.0753,
         0.0753,  0.2048,  0.2048,  0.2048,  0.2048,  0.2048,  0.2048,  0.2048,
         0.2048,  0.2048,  0.2048,  0.2048]),
indices=tensor([2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 2, 0, 0,
        0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]))
torch.return_types.max(
values=tensor([ 0.1940,  0.1928,  0.1928,  0.1902,  0.1902,  0.1923,  0.1923,  0.1923,
         0.1923,  0.1923,  0.1923, -0.0361, -0.0354, -0.0350, -0.0352, -0.0353,
        -0.0353, -0.0352, -0.0352, -0.0352, -0.0354, -0.0355,  0.2694,  0.2694,
         0.2694,  0.2694,  0.2694,  0.2694,  0.2694,  0.2694,  0.2694,  0.2694,
         0.269